# Warning: old version, replaced by onroerend_erfgoed_notas_auto.py


In [1]:
#!pip install pyproj
#!pip install -U numpy==1.26.4
#!pip install transformers
#!pip install -U accelerate
#!pip install pandas
#!pip install PyPDF2
#!pip install NLTK
#!pip install editdistance
#!pip install paramiko

#import nltk
#nltk.download('punkt')

In [1]:
# import libraries
import urllib.request
import requests
import json
from pyproj import Transformer
import os
import time
import sys

# import common functions
sys.path.insert(1, '../')
import common

# set up transformer from Lambert72 to lat/lon
transformer = Transformer.from_crs("EPSG:31370", "EPSG:4326")

# set name of module, to fetch info from config
module_name = "onroerend_erfgoed_notas"

/home/alex/anaconda3/envs/agnes-bert-file-import/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


False
cuda gpu number is 0


Some weights of the model checkpoint at alexbrandsen/ArcheoBERTje-NER were not used when initializing BertForTokenClassification: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight']
- This IS expected if you are initializing BertForTokenClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForTokenClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
/home/alex/anaconda3/envs/agnes-bert-file-import/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more 

In [2]:
# get info from config file

config = common.get_config()
        
last_indexed_id = config['data_source'][module_name]['last_indexed_id']
print(f'last indexed id: {last_indexed_id}')

endpoint_url = config['data_source'][module_name]['endpoint_url']
print(f'endpoint_url: {endpoint_url}')

pdf_folder = config['data_source'][module_name]['pdf_folder']
print(f'pdf_folder: {pdf_folder}')

json_folder = config['data_source'][module_name]['json_folder']
print(f'json_folder: {json_folder}')

html_folder = config['data_source'][module_name]['html_folder']
print(f'html_folder: {html_folder}')

language = config['data_source'][module_name]['language']
print(f'language: {language}')


bert_model = config['bert_models'][language]
print(f'bert_model: {bert_model}')

last indexed id: 30087
endpoint_url: https://loket.onroerenderfgoed.be/archeologie/notas/notas/
pdf_folder: /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/
json_folder: /media/alex/Data/agnes_data/onroerend_erfgoed_notas/json/
html_folder: /media/alex/Data/agnes_data/onroerend_erfgoed_notas/html/
language: dutch
bert_model: /media/alex/Data/agnes_models/ArcheoBERTje-NER


In [3]:
# set headers
headers = {'Accept': 'application/json', 
           'User-Agent': 'python-requests/2.18.1',
           'From': 'a.brandsen@arch.leidenuniv.nl (EXALT)'  
          }

# set parameters
params = {'per_pagina': 100, # number of results per page
          'sort': 'id',
          #'pagina': 1 # page 
         }   


In [4]:
# Create a requests Session
session = requests.Session()

# Set the header options
session.headers.update(headers)

# Make a request and store the response
try:
    response = session.get(endpoint_url, params=params)
    response.raise_for_status()                 # Raise error in case of failure 
except requests.exceptions.HTTPError as httpErr: 
    print ("HTTP Error:",httpErr) 
except requests.exceptions.ConnectionError as connErr: 
    print ("Error Connecting:",connErr) 
except requests.exceptions.Timeout as timeOutErr: 
    print ("Timeout Error:",timeOutErr) 
except requests.exceptions.RequestException as reqErr: 
    print ("Something Else:",reqErr)
    
# get json data from request
data = response.json()

# Fetch all the other pages of results
while 'next' in response.links:
    # GET the url pointing to the next page
    response = session.get(response.links['next']['url'])
    # add the data from the next page to the data we're collecting
    data.extend(response.json())
    # Sleep for half a second, so we don't overload the server
    time.sleep(0.5)
  
print(len(data))

26066


In [3]:
# import pickle

# file_path = 'data.pickle'




In [ ]:
# # Open the file in binary mode
# with open(file_path, 'wb') as file:
#     # Serialize and write the variable to the file
#     pickle.dump(data, file)


In [4]:
# Open the file in binary mode
# with open(file_path, 'rb') as file:
#     # Deserialize and retrieve the variable from the file
#     data = pickle.load(file)

In [5]:
# go through projects
for project in data:
    
    #print(json.dumps(project, indent=4))

    # if not fetched yet
    if project['id'] > last_indexed_id:

        print(f"Processing id:{project['id']}")
    
        # get more details on project using uri
        response = requests.get(
            project['uri'],
            headers = {'Accept': 'application/json'}
        )
        project_detail = response.json()

        #print(json.dumps(project_detail, sort_keys=True, indent=4))

        # loop through relevant documents, make document.json for each
        if 'bijlagen' in project_detail: 
            for doc in project_detail['bijlagen']:
    
                #print(json.dumps(doc, sort_keys=True, indent=4))
                
                if doc['bijlagetype']['id'] == 2 and doc['bestandsnaam'][-3:].lower() == 'pdf' and 'geplande werken' not in doc['bestandsnaam'].lower() and 'ontwerpplan' not in doc['bestandsnaam'].lower(): # is report and is pdf file
                    #print(doc['bestandsnaam'])
    
                    file_name = doc['bestandsnaam'].replace(' ','_').replace('(','').replace(')','')
    
                    output_document = {}
                    output_document['source'] = module_name
                    output_document['file_name'] = file_name
                    output_document['file_type'] = 'report'
                    if(doc['omschrijving']):
                        title = f"{project['onderwerp']} - {doc['omschrijving']}"
                    else:
                        title = f"{project['onderwerp']}"
                    output_document['title'] = title
                    creators = []
                    for auteur in doc['auteurs']:
                        creators.append(auteur['auteur'])
                    output_document['creators'] = creators
                    output_document['description'] = '' # no descriptions in this data source
                    output_document['publisher'] = project['archeoloog']
                    output_document['createdAt'] = project['datum_melden'][:10]
                    output_document['identifiers'] = {'uri':project['uri'],'oe_id':project['id']}
                    output_document['language'] = 'Dutch'
    
                    #coordinates
                    totalX = 0
                    totalY = 0
                    coordinates = project_detail['locatie']['contour']['coordinates'][0][0]
                    for coord in coordinates:
                        totalX += coord[0]
                        totalY += coord[1]
                    coordX = totalX / len(coordinates)
                    coordY = totalY / len(coordinates)
                    lat, lon = transformer.transform(coordX,coordY)
                    output_document['coordX'] = coordX
                    output_document['coordY'] = coordY
                    output_document['location'] = {'lat':lat,'lon':lon}
    
                    #print(json.dumps(output_document, indent=4))
    
                    # set document identifier
                    doc_id = f"{project['id']}_{file_name.replace('.pdf','')}"
    
                    print(f"doc_id:{doc_id}")
    
                    # save document.json 
                    json_output_folder = f"{json_folder}/{doc_id}"
                    common.savejson(output_document, f"{json_output_folder}/document.json")
    
                    print(f"saved doc json")
    
                    # download pdf
                    file_url = doc['url']
                    pdf_location = common.downloaddocument(file_url, project['id'], pdf_folder, file_name)
    
                    print(f"downloaded pdf")

                    
                    # process pdf, store page.json files with entities 
                    common.run_ner_on_pdf(
                        pdf_location, 
                        json_output_folder, 
                        bert_model, 
                        language
                    )

                    
                    
                    print(f"ran NER, saved page json")
    
                    # process pdf, save html files
                    html_output_folder = f"{html_folder}/{doc_id}"
                    common.pdf2html(pdf_location, html_output_folder)
    
                    print(f"generated and saved html")
    
                    # save last id we indexed in the settings file 
                    # (do this in the loop instead of after, in case we get errors/hanging that ends the script before we get to the end)
                    common.update_config(module_name, 'last_indexed_id', project['id'])
                    
                    print(f"updated config with latest id: {project['id']}")

                
# upload json and html to webserver
common.upload2webserver(json_folder, html_folder, module_name, config['webserver']['json_folder'], config['webserver']['html_folder'])

print(f"uploaded json/html to webserver")

# remotely start indexing script on webserver
common.start_index(module_name)

print(f"indexing on webserver started")

print(f"done!")



Processing id:30088
doc_id:30088_Rapport2085AalstKattestraat65-67
saved doc json
downloaded pdf


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/30088_Rapport2085AalstKattestraat65-67.pdf to html!
generated and saved html
updated config with latest id: 30088
Processing id:30090
doc_id:30090_2023-518_Herk_de_Stad_Grote_Baan_20c_VVR
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/30090_2023-518_Herk_de_Stad_Grote_Baan_20c_VVR.pdf to html!
generated and saved html
updated config with latest id: 30090
Processing id:30092
doc_id:30092_2404.1_VVR_Ottenburg_Tomme_Fluvius_v2
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/30092_2404.1_VVR_Ottenburg_Tomme_Fluvius_v2.pdf to html!
generated and saved html
updated config with latest id: 30092
Processing id:30093
doc_id:30093_DIME01_2024F149_Archeologienota_VvR_20240613
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_d

Superfluous whitespace found in object header b'2' b'0'
Superfluous whitespace found in object header b'3' b'0'
Superfluous whitespace found in object header b'25' b'0'
Superfluous whitespace found in object header b'37' b'0'
Superfluous whitespace found in object header b'40' b'0'
Superfluous whitespace found in object header b'59' b'0'
Superfluous whitespace found in object header b'72' b'0'
Superfluous whitespace found in object header b'76' b'0'
Superfluous whitespace found in object header b'80' b'0'
Superfluous whitespace found in object header b'83' b'0'
Superfluous whitespace found in object header b'88' b'0'
Superfluous whitespace found in object header b'92' b'0'
Superfluous whitespace found in object header b'97' b'0'
Superfluous whitespace found in object header b'105' b'0'
Superfluous whitespace found in object header b'109' b'0'
Superfluous whitespace found in object header b'113' b'0'
Superfluous whitespace found in object header b'117' b'0'
Superfluous whitespace found 

downloaded pdf


...

ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/32246_2024-0347_Asse_Koensborre_N_VvR.pdf to html!
generated and saved html
updated config with latest id: 32246
Processing id:32247
doc_id:32247_2025-0243_Oud-Turnhout_De_Liereman_Rode_Goor_zone_2_AB_fase_1_VvR
saved doc json


Superfluous whitespace found in object header b'1' b'0'
Superfluous whitespace found in object header b'2' b'0'
Superfluous whitespace found in object header b'3' b'0'
Superfluous whitespace found in object header b'28' b'0'
Superfluous whitespace found in object header b'47' b'0'
Superfluous whitespace found in object header b'66' b'0'
Superfluous whitespace found in object header b'77' b'0'
Superfluous whitespace found in object header b'97' b'0'
Superfluous whitespace found in object header b'101' b'0'
Superfluous whitespace found in object header b'106' b'0'
Superfluous whitespace found in object header b'109' b'0'
Superfluous whitespace found in object header b'120' b'0'
Superfluous whitespace found in object header b'125' b'0'
Superfluous whitespace found in object header b'128' b'0'
Superfluous whitespace found in object header b'132' b'0'
Superfluous whitespace found in object header b'135' b'0'
Superfluous whitespace found in object header b'140' b'0'
Superfluous whitespace fo

downloaded pdf


Superfluous whitespace found in object header b'119' b'0'
Superfluous whitespace found in object header b'117' b'0'
Superfluous whitespace found in object header b'116' b'0'
Superfluous whitespace found in object header b'115' b'0'
Superfluous whitespace found in object header b'118' b'0'
Superfluous whitespace found in object header b'124' b'0'
Superfluous whitespace found in object header b'123' b'0'
Superfluous whitespace found in object header b'121' b'0'
Superfluous whitespace found in object header b'122' b'0'
Superfluous whitespace found in object header b'127' b'0'
Superfluous whitespace found in object header b'126' b'0'
Superfluous whitespace found in object header b'131' b'0'
Superfluous whitespace found in object header b'130' b'0'
Superfluous whitespace found in object header b'129' b'0'
Superfluous whitespace found in object header b'134' b'0'
Superfluous whitespace found in object header b'133' b'0'
Superfluous whitespace found in object header b'139' b'0'
Superfluous wh

ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/32247_2025-0243_Oud-Turnhout_De_Liereman_Rode_Goor_zone_2_AB_fase_1_VvR.pdf to html!
generated and saved html
updated config with latest id: 32247
Processing id:32249
doc_id:32249_2025A56_verslag_van_resultaten
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/32249_2025A56_verslag_van_resultaten.pdf to html!
generated and saved html
updated config with latest id: 32249
Processing id:32250
doc_id:32250_2024J56_KALMTHOUT_HEIKEN-VVR
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoed_notas/pdf/32250_2024J56_KALMTHOUT_HEIKEN-VVR.pdf to html!
generated and saved html
updated config with latest id: 32250
Processing id:32251
doc_id:32251_36897_Kortenaken_VVR_fase2_v2
saved doc json
downloaded pdf
ran NER, saved page json
Converted /media/alex/Data/agnes_data/onroerend_erfgoe

In [ ]:
# get more details on project using uri
response = requests.get(
    'https://loket.onroerenderfgoed.be/archeologie/notas/notas/44',
    headers = {'Accept': 'application/json'}
)
project_detail = response.json()

In [ ]:
print(project_detail)

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.3/44.3 kB 905.1 kB/s eta 0:00:00MB/s eta 0:00:01
  Preparing metadata (setup.py) ... done
  Created wheel for func_timeout: filename=func_timeout-4.3.5-py3-none-any.whl size=15076 sha256=87442c24905d0d8b566b1a1bfce1a694a82e86036dbae2e2e2424956ca50144f
  Stored in directory: /home/alex/.cache/pip/wheels/07/e6/86/f23164d12c3134966614102db8e7956ab359faf7ffd78703ce
Successfully built func_timeout


terminated
